# Spectral Analysis - Swath

In [ ]:
import subprocess

import distributed

# Guessing installed cluster type
c = subprocess.run("qstat", capture_output=True, shell=True)

if c.returncode != 0:
    cluster_type = "slurm"
else:
    cluster_type = "sge"

In [ ]:
from casys.readers import ScCollectionReader
from octantng.core.dask import DaskCluster

from casys import CasysPlot, DataParams, Field, PlotParams, SwathData

In [ ]:
dask_cluster = DaskCluster(cluster_type=cluster_type, jobs=(5, 5), memory=8)

dask_client = dask_cluster.client
dask_cluster.wait_for_workers(n_workers=3, timeout=600)

## Reader and container definition

In [ ]:
collection_path = "/data/OCTANT_NG/tests/ce_swot/zcollection/"

reader = ScCollectionReader(
    data_path=collection_path,
    backend_kwargs={"cycle_numbers": 8},
    longitude="longitude",
    latitude="latitude",
)

In [ ]:
sd = SwathData(source=reader)

## Definition of the spectral analysis diagnostic

Using the [add_spectral_analysis](../generated/casys.computation.rst#casys.computation.SwathData.add_spectral_analysis) method:

In [ ]:
ssh_e = Field(
    name="ssh_karin_w_error",
    source=(
        "simulated_true_ssh_karin + simulated_error_karin + "
        "simulated_error_timing + simulated_error_roll + simulated_error_phase"
    ),
)

In [ ]:
sd.add_spectral_analysis(
    name="SSH Karin Spectral",
    field=ssh_e,
    segment_length=1024,
    holes_max_length=64,
    res_segments=True,
    res_individual_psd=True,
    pixels=[20, 49, [55, 60]],
    spectral_conf={
        "Periodogram, Tukey (alpha=0.2)": {
            "spectral_type": "periodogram",
            "detrend": "linear",
            "window": ("tukey", 0.2),
        },
    },
    pixels_selection="range",
    pixels_reduction="mean",
)

## Computation

In [ ]:
sd.compute_dask()

## Plotting

### PSD

In [ ]:
plot_psd_1 = CasysPlot(
    data=sd,
    data_name="SSH Karin Spectral",
    plot="PSD",
    plot_params=PlotParams(grid=True),
    spectral_name="Periodogram, Tukey (alpha=0.2)",
    pixel=20,
    second_axis=True,
)
plot_psd_1.add_stat_bar()

plot_psd_2 = CasysPlot(
    data=sd,
    data_name="SSH Karin Spectral",
    plot="PSD",
    plot_params=PlotParams(grid=True, line_style="", marker_size=4),
    spectral_name="Periodogram, Tukey (alpha=0.2)",
    pixel=49,
)
plot_psd_2.add_stat_bar()

plot_psd_3 = CasysPlot(
    data=sd,
    data_name="SSH Karin Spectral",
    plot="PSD",
    plot_params=PlotParams(grid=True, line_style="", marker_size=4),
    spectral_name="Periodogram, Tukey (alpha=0.2)",
    pixel=[55, 60],
)
plot_psd_3.add_stat_bar()

plot_psd_1.add_plot(plot_psd_2)
plot_psd_1.add_plot(plot_psd_3)
plot_psd_1.show()

In [ ]:
plot_psd_1 = CasysPlot(
    data=sd,
    data_name="SSH Karin Spectral",
    plot="PSD",
    spectral_name="Periodogram, Tukey (alpha=0.2)",
    pixel=20,
    plot_params=PlotParams(grid=True, marker_style="o", marker_size=3, color="red"),
    second_axis=True,
)
plot_psd_1.add_stat_bar()

plot_psd_2 = CasysPlot(
    data=sd,
    data_name="SSH Karin Spectral",
    plot="PSD",
    plot_params=PlotParams(grid=True),
    spectral_name="Periodogram, Tukey (alpha=0.2)",
    pixel=20,
    individual=True,
    n_bins_psd=75,
)
plot_psd_1.add_plot(plot_psd_2)

plot_psd_1.show()

### SEGMENTS

In [ ]:
plot_segments = CasysPlot(
    data=sd,
    data_name="SSH Karin Spectral",
    plot="SEGMENTS",
    plot_params=PlotParams(grid=True),
    data_params=DataParams(points_min_radius=0.5),
    pixel=20,
)
plot_segments.show()

In [ ]:
dask_cluster.close()

To learn more about spectral analysis diagnostic definition, please visit this documentation [page](../diagnostics/spectral_analysis.rst).